# Using LAMMPS with iPython and Jupyter

LAMMPS can be run interactively using iPython easily. This tutorial shows how to set this up.

## Installation

1. Download the latest version of LAMMPS into a folder (we will calls this `$LAMMPS_DIR` from now on)
2. Compile LAMMPS as a shared library and enable exceptions and PNG support
   ```bash
   cd $LAMMPS_DIR/src
   python Make.py -m mpi -png -s exceptions -a file
   make mode=shlib auto
   ```

3. Create a python virtualenv
   ```bash
   virtualenv testing
   source testing/bin/activate
   ```

4. Inside the virtualenv install the lammps package
   ```
   (testing) cd $LAMMPS_DIR/python
   (testing) python install.py
   (testing) cd   # move to your working directory
   ```

5. Install jupyter and ipython in the virtualenv
   ```bash
   (testing) pip install ipython jupyter
   ```

6. Run jupyter notebook
   ```bash
   (testing) jupyter notebook
   ```

## Example

In [ ]:
from lammps import IPyLammps

In [ ]:
L = IPyLammps()

In [ ]:
# 3d Lennard-Jones melt

L.units("lj")
L.atom_style("atomic")
L.atom_modify("map array")

L.lattice("fcc", 0.8442)
L.region("box block", 0, 4, 0, 4, 0, 4)
L.create_box(1, "box")
L.create_atoms(1, "box")
L.mass(1, 1.0)

L.velocity("all create", 1.44, 87287, "loop geom")

L.pair_style("lj/cut", 2.5)
L.pair_coeff(1, 1, 1.0, 1.0, 2.5)

L.neighbor(0.3, "bin")
L.neigh_modify("delay 0 every 20 check no")

L.fix("1 all nve")

L.variable("fx atom fx")

L.run(10)

In [ ]:
L.image(zoom=1)

## Queries about LAMMPS simulation

In [ ]:
L.system

In [ ]:
L.system.natoms

In [ ]:
L.communication

In [ ]:
L.fixes

In [ ]:
L.computes

In [ ]:
L.dumps

In [ ]:
L.groups

## Working with LAMMPS Variables

In [ ]:
L.variable("a index 2")

In [ ]:
L.variables

In [ ]:
L.variable("t equal temp")

In [ ]:
L.variables

In [ ]:
import sys

if sys.version_info < (3, 0):
    # In Python 2 'print' is a restricted keyword, which is why you have to use the lmp_print function instead.
    x = float(L.lmp_print('"${a}"'))
else:
    # In Python 3 the print function can be redefined.
    # x = float(L.print('"${a}"')")
    
    # To avoid a syntax error in Python 2 executions of this notebook, this line is packed into an eval statement
    x = float(eval("L.print('\"${a}\"')"))
x

In [ ]:
L.variables['t'].value

In [ ]:
L.eval("v_t/2.0")

In [ ]:
L.variable("b index a b c")

In [ ]:
L.variables['b'].value

In [ ]:
L.eval("v_b")

In [ ]:
L.variables['b'].definition

In [ ]:
L.variable("i loop 10")

In [ ]:
L.variables['i'].value

In [ ]:
L.next("i")
L.variables['i'].value

In [ ]:
L.eval("ke")

## Accessing Atom data

In [ ]:
L.atoms[0]

In [ ]:
[x for x in dir(L.atoms[0]) if not x.startswith('__')]

In [ ]:
L.atoms[0].position

In [ ]:
L.atoms[0].id

In [ ]:
L.atoms[0].velocity

In [ ]:
L.atoms[0].force

In [ ]:
L.atoms[0].type

In [ ]:
L.variables['fx'].value

## Accessing thermo data

In [ ]:
L.runs

In [ ]:
L.runs[0]

In [ ]:
L.runs[0].thermo

In [ ]:
L.runs[0].thermo.Temp

## Saving session to as LAMMPS input file

In [ ]:
L.write_script("in.output")